In [1]:
import pandas as pd
import numpy as np

import plotly.offline as py
import plotly.express as px
import plotly.graph_objects as goz

import plotly.figure_factory as ff

import warnings
warnings.filterwarnings('ignore')

py.init_notebook_mode(connected=True)
pd.set_option('display.float_format', lambda x: '%.2f' % x)

Error importing optional module geopandas
Traceback (most recent call last):
  File "/opt/anaconda3/lib/python3.9/site-packages/_plotly_utils/optional_imports.py", line 30, in get_module
    return import_module(name)
  File "/opt/anaconda3/lib/python3.9/importlib/__init__.py", line 127, in import_module
    return _bootstrap._gcd_import(name[level:], package, level)
  File "<frozen importlib._bootstrap>", line 1030, in _gcd_import
  File "<frozen importlib._bootstrap>", line 1007, in _find_and_load
  File "<frozen importlib._bootstrap>", line 986, in _find_and_load_unlocked
  File "<frozen importlib._bootstrap>", line 680, in _load_unlocked
  File "<frozen importlib._bootstrap_external>", line 850, in exec_module
  File "<frozen importlib._bootstrap>", line 228, in _call_with_frames_removed
  File "/opt/anaconda3/lib/python3.9/site-packages/geopandas/__init__.py", line 1, in <module>
    from geopandas._config import options  # noqa
  File "/opt/anaconda3/lib/python3.9/site-packages/g

In [2]:
df=pd.read_csv("ceo_data_pay_merged_sp500.csv")
df = df.loc[:, ~df.columns.str.contains('^Unnamed')]

In [3]:
df.head()

ticker                  company_name median_worker_pay pay_ratio  \
0   ATVI     Activision Blizzard, Inc.          $117,207       7:1   
1   CHTR  Charter Communications, Inc.           $60,007     698:1   
2  CMCSA           Comcast Corporation           $83,840     405:1   
3    DIS       The Walt Disney Company           $50,430     644:1   
4  DISCA  Warner Bros. Discovery, Inc.           $82,964   2,972:1   

          ceo_name        salary                  industry  
0    Robert Kotick      $826,549  Communication%20Services  
1  Thomas Rutledge   $41,860,263  Communication%20Services  
2    Brian Roberts   $33,978,581  Communication%20Services  
3    Robert Chapek   $32,464,293  Communication%20Services  
4     David Zaslav  $246,573,481  Communication%20Services

### Cleaning Data

In [4]:
df["industry"] = df["industry"].str.replace(r'[^a-zA-Z_]', ' ', regex=True)
df["industry"] = df["industry"].replace(r'\s+', ' ', regex=True)

df["median_worker_pay"] = df["median_worker_pay"].str.replace(r"[$,]", "", regex=True)
df["median_worker_pay"] = pd.to_numeric(df["median_worker_pay"], errors="coerce")

df["salary"] = df["salary"].str.replace(r"[$,]", "", regex=True)
df["salary"] = pd.to_numeric(df["salary"], errors="coerce")

df["pay_ratio"]=df["pay_ratio"].str.split(':1').str[0]
df["pay_ratio"].replace(',','', regex=True, inplace=True)
df["pay_ratio"] = pd.to_numeric(df["pay_ratio"], errors="coerce")

In [5]:
df.sort_values(['salary'],ascending=False)

ticker                         company_name  median_worker_pay  pay_ratio  \
40    EXPE                  Expedia Group, Inc.             102270       2897   
4    DISCA         Warner Bros. Discovery, Inc.              82964       2972   
23    AMZN                     Amazon.com, Inc.              32855       6474   
362   INTC                    Intel Corporation             104400       1711   
376    NOW                     ServiceNow, Inc.             233859        709   
..     ...                                  ...                ...        ...   
281   FAST                     Fastenal Company              40843         59   
0     ATVI            Activision Blizzard, Inc.             117207          7   
410   CTVA                        Corteva, Inc.              85572        166   
145  BRK.B              Berkshire Hathaway Inc.              58881          6   
20    TTWO  Take-Two Interactive Software, Inc.              70096          2   

              ceo_name     salary                industry  
40          Peter Kern  296247749  Consumer Discretionary  
4         David Zaslav  246573481  Communication Services  
23        Andrew Jassy  212701169  Consumer Discretionary  
362  Patrick Gelsinger  178590400  Information Technology  
376  William McDermott  165802037  Information Technology  
..                 ...        ...                     ...  
281    Daniel Florness    2423614             Industrials  
0        Robert Kotick     826549  Communication Services  
410      Charles Magro     792786               Materials  
145     Warren Buffett     373204              Financials  
20     Strauss Zelnick     142996  Communication Services  

[492 rows x 7 columns]

### Feature Engineering

In [6]:
import yfinance as yf
pd.set_option('display.max_rows', None)

industry=[]
sector=[]
fullTimeEmployees=[]
longBusinessSummary=[]
totalRevenue=[]
grossProfits=[]
freeCashflow=[]
operatingCashflow=[]
for i,ticker_i in enumerate(df["ticker"]):
#     try:
    ticker=yf.Ticker(str(ticker_i))
    print(i,ticker)

    try:
        industry.append(ticker.info["industry"])
    except:
#         print("industry-Issue",ticker)
        industry.append("Issue")

    try:
        sector.append(ticker.info["sector"])
    except:
#         print("sector-Issue",ticker)
        sector.append("Issue")

    try:
        fullTimeEmployees.append(ticker.info["fullTimeEmployees"])
    except:
#         print("fullTimeEmployees-Issue",ticker)
        fullTimeEmployees.append(np.nan)

    try:
        longBusinessSummary.append(ticker.info["longBusinessSummary"])
    except:
#         print("longBusinessSummary-Issue",ticker)
        longBusinessSummary.append("Issue")

    try:
        totalRevenue.append(ticker.info["totalRevenue"])
    except:
#         print("totalRevenue-Issue",ticker)
        totalRevenue.append(np.nan)

    try:
        grossProfits.append(ticker.info["grossProfits"])
    except:
#         print("grossProfits-Issue",ticker)
        grossProfits.append(np.nan)

    try:
        freeCashflow.append(ticker.info["freeCashflow"])
    except:
#         print("freeCashflow-Issue",ticker)
        freeCashflow.append(np.nan)

    try:
        operatingCashflow.append(ticker.info["operatingCashflow"])
    except:
#         print("operatingCashflow-Issue",ticker)
        operatingCashflow.append(np.nan)
#     except:
#         print("Issue",ticker)
#         industry.append("Issue")
#         sector.append("Issue")
#         fullTimeEmployees.append("Issue")
#         longBusinessSummary.append("Issue")
#         totalRevenue.append("Issue")
#         grossProfits.append("Issue")
#         freeCashflow.append("Issue")
#         operatingCashflow.append("Issue")

0 yfinance.Ticker object <ATVI>
1 yfinance.Ticker object <CHTR>
2 yfinance.Ticker object <CMCSA>
3 yfinance.Ticker object <DIS>
4 yfinance.Ticker object <DISCA>
5 yfinance.Ticker object <DISH>
6 yfinance.Ticker object <EA>
7 yfinance.Ticker object <FOXA>
8 yfinance.Ticker object <GOOGL>
9 yfinance.Ticker object <IPG>
10 yfinance.Ticker object <LUMN>
11 yfinance.Ticker object <LYV>
12 yfinance.Ticker object <META>
13 yfinance.Ticker object <MTCH>
14 yfinance.Ticker object <NFLX>
15 yfinance.Ticker object <NWSA>
16 yfinance.Ticker object <OMC>
17 yfinance.Ticker object <PARA>
18 yfinance.Ticker object <T>
19 yfinance.Ticker object <TMUS>
20 yfinance.Ticker object <TTWO>
21 yfinance.Ticker object <VZ>
22 yfinance.Ticker object <AAP>
23 yfinance.Ticker object <AMZN>
24 yfinance.Ticker object <APTV>
25 yfinance.Ticker object <AZO>
26 yfinance.Ticker object <BBWI>
27 yfinance.Ticker object <BBY>
28 yfinance.Ticker object <BKNG>
29 yfinance.Ticker object <BWA>
30 yfinance.Ticker object <CCL>


251 yfinance.Ticker object <UHS>
252 yfinance.Ticker object <UNH>
253 yfinance.Ticker object <VRTX>
254 yfinance.Ticker object <VTRS>
255 yfinance.Ticker object <WAT>
256 yfinance.Ticker object <WST>
257 yfinance.Ticker object <XRAY>
258 yfinance.Ticker object <ZBH>
259 yfinance.Ticker object <ZTS>
260 yfinance.Ticker object <AAL>
261 yfinance.Ticker object <ALK>
262 yfinance.Ticker object <ALLE>
263 yfinance.Ticker object <AME>
264 yfinance.Ticker object <AOS>
265 yfinance.Ticker object <BA>
266 yfinance.Ticker object <CARR>
267 yfinance.Ticker object <CAT>
268 yfinance.Ticker object <CHRW>
269 yfinance.Ticker object <CMI>
270 yfinance.Ticker object <CPRT>
271 yfinance.Ticker object <CSGP>
272 yfinance.Ticker object <CSX>
273 yfinance.Ticker object <CTAS>
274 yfinance.Ticker object <DAL>
275 yfinance.Ticker object <DE>
276 yfinance.Ticker object <DOV>
277 yfinance.Ticker object <EFX>
278 yfinance.Ticker object <EMR>
279 yfinance.Ticker object <ETN>
280 yfinance.Ticker object <EXPD>
28

In [7]:
df["industry"]=industry
df["sector"]=sector
df["fullTimeEmployees"]=fullTimeEmployees
df["longBusinessSummary"]=longBusinessSummary
df["totalRevenue"]=totalRevenue
df["grossProfits"]=grossProfits
df["freeCashflow"]=freeCashflow
df["operatingCashflow"]=operatingCashflow

In [8]:
df.dtypes

ticker                  object
company_name            object
median_worker_pay        int64
pay_ratio                int64
ceo_name                object
salary                   int64
industry                object
sector                  object
fullTimeEmployees      float64
longBusinessSummary     object
totalRevenue           float64
grossProfits           float64
freeCashflow           float64
operatingCashflow      float64
dtype: object

In [9]:
df_before_na = df.copy(deep=True)

In [10]:
df=df.fillna(0)
# df=df.dropna()

In [11]:
df.head(10)

ticker                              company_name  median_worker_pay  \
0   ATVI                 Activision Blizzard, Inc.             117207   
1   CHTR              Charter Communications, Inc.              60007   
2  CMCSA                       Comcast Corporation              83840   
3    DIS                   The Walt Disney Company              50430   
4  DISCA              Warner Bros. Discovery, Inc.              82964   
5   DISH                  DISH Network Corporation              58161   
6     EA                      Electronic Arts Inc.             115569   
7   FOXA                           Fox Corporation              91803   
8  GOOGL                             Alphabet Inc.             295884   
9    IPG  The Interpublic Group of Companies, Inc.              59814   

   pay_ratio            ceo_name     salary                        industry  \
0          7       Robert Kotick     826549  Electronic Gaming & Multimedia   
1        698     Thomas Rutledge   41860263                Telecom Services   
2        405       Brian Roberts   33978581                Telecom Services   
3        644       Robert Chapek   32464293                   Entertainment   
4       2972        David Zaslav  246573481                           Issue   
5         50          W. Carlson    2895882                Telecom Services   
6        172       Andrew Wilson   19858539  Electronic Gaming & Multimedia   
7        237     Lachlan Murdoch   21748681                   Entertainment   
8         21       Sundar Pichai    6322599  Internet Content & Information   
9        290  Philippe Krakowsky   17371647            Advertising Agencies   

                   sector  fullTimeEmployees  \
0  Communication Services           13000.00   
1  Communication Services          101700.00   
2  Communication Services          186000.00   
3  Communication Services          171600.00   
4                   Issue               0.00   
5  Communication Services           14200.00   
6  Communication Services               0.00   
7  Communication Services           10600.00   
8  Communication Services          190711.00   
9  Communication Services           58200.00   

                                 longBusinessSummary    totalRevenue  \
0  Activision Blizzard, Inc., together with its s...   8143000064.00   
1  Charter Communications, Inc. operates as a bro...  54475001856.00   
2  Comcast Corporation operates as a media and te... 120107999232.00   
3  The Walt Disney Company, together with its sub...  84414996480.00   
4                                              Issue            0.00   
5  DISH Network Corporation, together with its su...  16305769472.00   
6  Electronic Arts Inc. develops, markets, publis...            0.00   
7  Fox Corporation operates as a news, sports, an...            0.00   
8  Alphabet Inc. offers various products and plat... 284612001792.00   
9  The Interpublic Group of Companies, Inc. provi...   9399100416.00   

     grossProfits   freeCashflow  operatingCashflow  
0   5306000000.00           0.00               0.00  
1  24485000000.00  4683125248.00     14600999936.00  
2  83214000000.00 10372875264.00     26383998976.00  
3  28321000000.00  4855750144.00      5248999936.00  
4            0.00           0.00               0.00  
5   5308332000.00 -1256952320.00      3124130048.00  
6            0.00           0.00               0.00  
7   4857000000.00           0.00               0.00  
8 156633000000.00 55862624256.00     89898000384.00  
9   3602300000.00   372637504.00       694800000.00

In [12]:
df.to_csv("SP500.csv",index=False)

In [13]:
import pandas as pd
import numpy as np

import plotly.express as px
import plotly.graph_objects as go

import plotly.offline as py

from plotly.subplots import make_subplots
import plotly.figure_factory as ff

pd.set_option('display.float_format', lambda x: '%.2f' % x)

df=pd.read_csv("SP500.csv")

### Univariate Analysis

In [14]:
# num_cols=df.select_dtypes(include=[np.number])

num_cols = list(df.select_dtypes(include = np.number).columns)

In [15]:
colorscale = [[0, '#1f77b4'],[.5, '#aec7e8'],[1, '#ff7f0e']]
fig = ff.create_table(round(df[num_cols].describe().reset_index(), 2), font_colors = ['white'], colorscale = colorscale)

for i in range(len(fig.layout.annotations)):
    fig.layout.annotations[i].font.size = 9
    
fig.update_layout(
    title_text = 'Descriptive Statistics on the numerical columns',
    margin = {'t':50},
    template= "plotly_dark"
)
    
fig.show()

In [16]:
# categorized_cols=df.select_dtypes(exclude=[object])

categorized_cols = list(df.select_dtypes(include = 'object').columns)

In [17]:
colorscale = [[0, '#1f77b4'],[.5, '#aec7e8'],[1, '#ff7f0e']]
fig = ff.create_table(df[categorized_cols].describe().reset_index(), font_colors = ['white'], colorscale = colorscale)

for i in range(len(fig.layout.annotations)):
    fig.layout.annotations[i].font.size = 9
    
fig.update_layout(
    title_text = 'Statistics of the categorical columns',
    margin = {'t':50},
    template= "plotly_dark"
)
    
fig.show()

In [18]:
num_cols

['median_worker_pay',
 'pay_ratio',
 'salary',
 'fullTimeEmployees',
 'totalRevenue',
 'grossProfits',
 'freeCashflow',
 'operatingCashflow']

In [19]:
def plot_histogram(col_name):
    series = df[col_name]
    # remove zero values items
    series = series[ series != 0 ]
    smin,smax = series.min(),series.max()
    # remove outliers for +- three standard deviations.
    series = series[ ~( ( series - series.mean() ).abs() > 3 * series.std() ) ]
    percentiles = [ np.percentile(series,n) for n in (2.5,50,97.5) ]
    
    trace0 = go.Histogram( x = series,
                            histfunc = 'avg', 
                            histnorm = 'probability density',
                            opacity=.75,
                            marker = {'color':'#EB89B5'})
    data_ = go.Data( [trace0] )
    
    shapes = [{ 'line': { 'color': '#0099FF', 'dash':'solid', 'width':2 },
                'type':'line',
                'x0':percentiles[0], 'x1':percentiles[0], 'xref':'x',
                'y0':-0.1, 'y1':1, 'yref':'paper' },
    { 'line': { 'color': '#00999F', 'dash':'solid', 'width':1 },
                'type':'line',
                'x0':percentiles[1], 'x1':percentiles[1], 'xref':'x',
                'y0':-0.1, 'y1':1, 'yref':'paper' },
    
              { 'line': { 'color': '#0099FF', 'dash':'solid', 'width':2 },
                'type':'line',
                'x0':percentiles[2], 'x1':percentiles[2], 'xref':'x',
                'y0':-0.1, 'y1':1, 'yref':'paper' } 
             ]
    
    annotations = [ {'x': percentiles[0], 'xref':'x','xanchor':'right',
                     'y': .3, 'yref':'paper', 
                     'text':'2.5%', 'font':{'size':16},
                     'showarrow':False},
                   
                    {'x': percentiles[1], 'xref':'x','xanchor':'center',
                     'y': .2, 'yref':'paper', 
                     'text':'95%<br>median = {0:,.2f}<br>mean = {1:,.2f}<br>min = {2:,}<br>max = {3:,}'
                         .format(percentiles[1],series.mean(),smin,smax), 
                     'showarrow':False,
                     'font':{'size':20} },
                   
    {'x': percentiles[2], 'xref':'x','xanchor':'left',
                     'y': .3, 'yref':'paper', 
                     'text':'2.5%','font':{'size':16}, 
                     'showarrow':False},
                   
                    {'x': .5, 'xref':'paper','xanchor':'center',
                     'y': 1.1, 'yref':'paper','yanchor':'middle', 
                     'text':'Outliers above or below three standard deviations are excluded from the graph, mean and median calculations.',
                     'font':{'size':15,'color':'mistyrose'}, 
                     'showarrow':False} 
                  ]
    
    layout = go.Layout( title = col_name.replace('_',' ').capitalize(),
                        titlefont = {'size':50},
                        yaxis = {'title':'Probability/Density'},
                        xaxis = {'title':col_name, 'type':'linear'},
                        shapes = shapes,
                         annotations = annotations
                         )
    figure = go.Figure(data = data_, layout = layout)
    py.iplot(figure)
    
def plot_histogram_without_outliers(col_name):
    series = df[col_name]
    # remove zero values items
    series = series[ series != 0 ]
    smin,smax = series.min(),series.max()
    # remove outliers for +- three standard deviations.
#     series = series[ ~( ( series - series.mean() ).abs() > 3 * series.std() ) ]
    percentiles = [ np.percentile(series,n) for n in (2.5,50,97.5) ]
    
    trace0 = go.Histogram( x = series,
                            histfunc = 'avg', 
                            histnorm = 'probability density',
                            opacity=.75,
                            marker = {'color':'#EB89B5'})
    data_ = go.Data( [trace0] )
    
    shapes = [{ 'line': { 'color': '#0099FF', 'dash':'solid', 'width':2 },
                'type':'line',
                'x0':percentiles[0], 'x1':percentiles[0], 'xref':'x',
                'y0':-0.1, 'y1':1, 'yref':'paper' },
    { 'line': { 'color': '#00999F', 'dash':'solid', 'width':1 },
                'type':'line',
                'x0':percentiles[1], 'x1':percentiles[1], 'xref':'x',
                'y0':-0.1, 'y1':1, 'yref':'paper' },
    
              { 'line': { 'color': '#0099FF', 'dash':'solid', 'width':2 },
                'type':'line',
                'x0':percentiles[2], 'x1':percentiles[2], 'xref':'x',
                'y0':-0.1, 'y1':1, 'yref':'paper' } 
             ]
    
    annotations = [ {'x': percentiles[0], 'xref':'x','xanchor':'right',
                     'y': .3, 'yref':'paper', 
                     'text':'2.5%', 'font':{'size':16},
                     'showarrow':False},
                   
                    {'x': percentiles[1], 'xref':'x','xanchor':'center',
                     'y': .2, 'yref':'paper', 
                     'text':'95%<br>median = {0:,.2f}<br>mean = {1:,.2f}<br>min = {2:,}<br>max = {3:,}'
                         .format(percentiles[1],series.mean(),smin,smax), 
                     'showarrow':False,
                     'font':{'size':20} },
                   
    {'x': percentiles[2], 'xref':'x','xanchor':'left',
                     'y': .3, 'yref':'paper', 
                     'text':'2.5%','font':{'size':16}, 
                     'showarrow':False},
                   
                    {'x': .5, 'xref':'paper','xanchor':'center',
                     'y': 1.1, 'yref':'paper','yanchor':'middle', 
                     'text':'Outliers above or below three standard deviations are excluded from the graph, mean and median calculations.',
                     'font':{'size':15,'color':'mistyrose'}, 
                     'showarrow':False} 
                  ]
    
    layout = go.Layout( title = col_name.replace('_',' ').capitalize(),
                        titlefont = {'size':50},
                        yaxis = {'title':'Probability/Density'},
                        xaxis = {'title':col_name, 'type':'linear'},
                        shapes = shapes,
                         annotations = annotations
                         )
    figure = go.Figure(data = data_, layout = layout)
    py.iplot(figure)
    
def plot_value_counts(col_name, table=False, bar=False):
    N=10
    df_grouped = df.groupby(col_name).apply(lambda x: [', '.join(list(x['company_name']))])
    df_grouped=df_grouped.to_frame('companies').reset_index()


    values_count = pd.DataFrame(df[col_name].value_counts())
    values_count.columns = ['count']
    # convert the index column into a regular column.
    values_count[col_name] = [ str(i) for i in values_count.index ]
    # add a column with the percentage of each data point to the sum of all data points.
    values_count['percent'] = values_count['count'].div(values_count['count'].sum()).multiply(100).round(2)
    # change the order of the columns.
    values_count=values_count.merge(df_grouped, left_on=col_name, right_on=col_name)

    values_count = values_count.reindex([col_name,'count','percent','companies'],axis=1)
    values_count.reset_index(drop=True,inplace=True)
    values_count=values_count.head(N)
    if bar:
        # add a font size for annotations0 which is relevant to the length of the data points.
        font_size = int(abs(20 - (.25 * len(values_count[col_name]))))
        
        trace0 = go.Bar(x=values_count[col_name], y=values_count['count'])
        data_ = go.Data([trace0])
        
        annotations0 = [dict(x=xi,
                             y=yi, 
                             showarrow=False,
                             font={'size':font_size},
                             text="{:,}".format(yi),
                             xanchor='center',
                             yanchor='bottom')
                        for xi,yi,_,_ in values_count.values]
        
        annotations1 = [dict(x=xi,
                             y=yi/2,
                             showarrow=False,
                             text="{}%".format(pi),
                             xanchor='center',
                             yanchor='middle',
                             font={'color':'yellow'})
                        for xi,yi,pi,_ in values_count.values if pi > 10]
        
        annotations = annotations0 + annotations1
        
        layout = go.Layout(title=col_name.replace('_',' ').capitalize(),
                           titlefont={'size':50},
                           yaxis={'title':'count'},
                           xaxis={'type':'category'},
                           annotations=annotations)
        figure = go.Figure(data=data_, layout=layout)
        figure.update_layout(height=800)
        py.iplot(figure)
    
    if table: 
        values_count['count'] = values_count['count'].apply(lambda d : "{:,}".format(d))
        table = ff.create_table(values_count,index_title="race")
        py.iplot(table)
    
    return values_count


In [20]:
for col in num_cols :
    plot_histogram(col)
    
for col in num_cols :
    plot_histogram_without_outliers(col)

In [21]:

import pandas as pd

# specify the column names and the number of rows to display
industry_col = 'industry'
company_col = 'company_name'
N = 10

# group the dataframe by industry and create a new column with a list of matching companies
df_grouped = df.groupby(industry_col).apply(lambda x: [', '.join(list(x[company_col]))])

df_grouped=df_grouped.to_frame('companies').reset_index()

# calculate the count and percentage of each unique industry value
values_count = pd.DataFrame(df[industry_col].value_counts())
values_count.columns = ['count']
values_count[industry_col] = [ str(i) for i in values_count.index ]
values_count['percent'] = values_count['count'].div(values_count['count'].sum()).multiply(100).round(2)

# join the list of matching companies to the corresponding industry value in a single column
values_count=values_count.merge(df_grouped, left_on='industry', right_on='industry')

# reorder the columns and display the top N rows
values_count = values_count.reindex([industry_col,'count','percent','companies'], axis=1)
values_count.reset_index(drop=True, inplace=True)
values_count = values_count.head(N)



In [22]:
values_count

industry  count  percent  \
0     Utilities—Regulated Electric     23     4.67   
1   Specialty Industrial Machinery     17     3.46   
2                   Semiconductors     14     2.85   
3                   Banks—Regional     14     2.85   
4           Diagnostics & Research     12     2.44   
5  Information Technology Services     12     2.44   
6                    Oil & Gas E&P     11     2.24   
7              Specialty Chemicals     10     2.03   
8              Aerospace & Defense     10     2.03   
9             Software—Application     10     2.03   

                                           companies  
0  [Ameren Corporation, American Electric Power C...  
1  [AMETEK, Inc., A. O. Smith Corporation, Cummin...  
2  [Analog Devices, Inc., Advanced Micro Devices,...  
3  [Citizens Financial Group, Inc., Comerica Inco...  
4  [Agilent Technologies, Inc., Charles River Lab...  
5  [Leidos Holdings, Inc., Accenture Plc, Broadri...  
6  [APA Corp., ConocoPhillips, Coterra Energy Inc...  
7  [Albemarle Corporation, Air Products and Chemi...  
8  [The Boeing Company, General Dynamics Corporat...  
9  [Autodesk, Inc., ANSYS, Inc., Ceridian HCM Hol...

In [23]:
fig = px.scatter_matrix(
    df,
    dimensions=["median_worker_pay", "pay_ratio", "salary", "fullTimeEmployees"],
    color="sector",
    hover_name=df["ceo_name"] + " - " + df["company_name"],
    title="SP500 Variables Scatter Plot Matrix",
)

fig.show()

In [24]:
categorized_cols

['ticker',
 'company_name',
 'ceo_name',
 'industry',
 'sector',
 'longBusinessSummary']

In [25]:
# Remove specific columns from the categorized_cols list
categorized_cols = [col for col in categorized_cols if col not in ['ticker', 'company_name', 'ceo_name', 'longBusinessSummary']]


In [26]:
df_cat=[]
for col in categorized_cols:
    values_count = plot_value_counts(col,1,1)
    df_cat.append(values_count)

### Bivariate Analysis

In [27]:
import plotly.express as px
px.scatter(df, x="median_worker_pay", y="salary",
size="fullTimeEmployees", color="company_name",hover_name="ticker")

In [28]:
px.scatter(df, x="pay_ratio", y="salary",
size="fullTimeEmployees", color="company_name",hover_name="ticker")

In [29]:
px.scatter(df, x="totalRevenue", y="salary",
size="fullTimeEmployees", color="company_name",hover_name="ticker")

In [30]:
px.scatter(df, x="grossProfits", y="salary",
size="fullTimeEmployees", color="company_name",hover_name="ticker")

In [31]:
px.scatter(df, x="freeCashflow", y="salary",
size="fullTimeEmployees", color="company_name",hover_name="ticker")

In [32]:
px.scatter(df, x="operatingCashflow", y="salary",
size="fullTimeEmployees", color="company_name",hover_name="ticker")